In [7]:
from __future__ import print_function, division

from keras.datasets import mnist
from keras.layers import Input, Dense, Reshape, Flatten, Dropout
from keras.layers import BatchNormalization, Activation
from keras.layers.advanced_activations import LeakyReLU

from keras.models import Sequential, Model
from keras.optimizers import Adam

import matplotlib.pyplot as plt

import sys

import numpy as np

In [14]:
class GAN():
    def __init__(self):
        self.img_rows = 28
        self.img_cols = 28
        self.channels = 1
        self.img_shape = (self.img_rows, self.img_cols, self.channels)
        self.latent_dim = 100

        optimizer = Adam(0.0002, 0.5)

        self.discriminator = self.build_discriminator()
        self.discriminator.compile(loss='binary_crossentropy',
            optimizer=optimizer,
            metrics=['accuracy'])

        self.generator = self.build_generator()

        z = Input(shape=(self.latent_dim,))
        img = self.generator(z)

        self.discriminator.trainable = False

        validity = self.discriminator(img)

        self.combined = Model(z, validity)
        self.combined.compile(loss='binary_crossentropy', optimizer=optimizer)


    def build_generator(self):

        model = Sequential()

        model.add(Dense(256, input_dim=self.latent_dim))
        model.add(LeakyReLU(alpha=0.2))
        model.add(BatchNormalization(momentum=0.8))
        model.add(Dense(512))
        model.add(LeakyReLU(alpha=0.2))
        model.add(BatchNormalization(momentum=0.8))
        model.add(Dense(1024))
        model.add(LeakyReLU(alpha=0.2))
        model.add(BatchNormalization(momentum=0.8))
        model.add(Dense(np.prod(self.img_shape), activation='tanh'))
        model.add(Reshape(self.img_shape))

        model.summary()

        noise = Input(shape=(self.latent_dim,))
        img = model(noise)

        return Model(noise, img)

    def build_discriminator(self):

        model = Sequential()

        model.add(Flatten(input_shape=self.img_shape))
        model.add(Dense(512))
        model.add(LeakyReLU(alpha=0.2))
        model.add(Dense(256))
        model.add(LeakyReLU(alpha=0.2))
        model.add(Dense(1, activation='sigmoid'))
        model.summary()

        img = Input(shape=self.img_shape)
        validity = model(img)

        return Model(img, validity)

    def train(self, epochs, batch_size=128, sample_interval=50):

        (X_train, _), (_, _) = mnist.load_data()

        X_train = X_train / 127.5 - 1.
        X_train = np.expand_dims(X_train, axis=3)

        valid = np.ones((batch_size, 1))
        fake = np.zeros((batch_size, 1))

        for epoch in range(epochs):

            idx = np.random.randint(0, X_train.shape[0], batch_size)
            imgs = X_train[idx]

            noise = np.random.normal(0, 1, (batch_size, self.latent_dim))

            gen_imgs = self.generator.predict(noise)

            d_loss_real = self.discriminator.train_on_batch(imgs, valid)
            d_loss_fake = self.discriminator.train_on_batch(gen_imgs, fake)
            d_loss = 0.5 * np.add(d_loss_real, d_loss_fake)

            

            noise = np.random.normal(0, 1, (batch_size, self.latent_dim))

            g_loss = self.combined.train_on_batch(noise, valid)

            print ("%d [D loss: %f, acc.: %.2f%%] [G loss: %f]" % (epoch, d_loss[0], 100*d_loss[1], g_loss))

            if epoch % sample_interval == 0:
                self.sample_images(epoch)

    def sample_images(self, epoch):
        r, c = 5, 5
        noise = np.random.normal(0, 1, (r * c, self.latent_dim))
        gen_imgs = self.generator.predict(noise)

        gen_imgs = 0.5 * gen_imgs + 0.5

        fig, axs = plt.subplots(r, c)
        cnt = 0
        for i in range(r):
            for j in range(c):
                axs[i,j].imshow(gen_imgs[cnt, :,:,0], cmap='gray')
                axs[i,j].axis('off')
                cnt += 1
        fig.savefig("/home/ceinfo/Desktop/im/image/images%d.png" % epoch)
        plt.close()


In [ ]:
if __name__ == '__main__':
    gan = GAN()
    gan.train(epochs=100000, batch_size=132, sample_interval=10000)

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
flatten_4 (Flatten)          (None, 784)               0         
_________________________________________________________________
dense_22 (Dense)             (None, 512)               401920    
_________________________________________________________________
leaky_re_lu_16 (LeakyReLU)   (None, 512)               0         
_________________________________________________________________
dense_23 (Dense)             (None, 256)               131328    
_________________________________________________________________
leaky_re_lu_17 (LeakyReLU)   (None, 256)               0         
_________________________________________________________________
dense_24 (Dense)             (None, 1)                 257       
Total params: 533,505
Trainable params: 533,505
Non-trainable params: 0
_________________________________________________________________
____

/usr/local/lib/python3.5/dist-packages/keras/engine/training.py:490: UserWarning: Discrepancy between trainable weights and collected trainable weights, did you set `model.trainable` without calling `model.compile` after ?
  'Discrepancy between trainable weights and collected trainable'


0 [D loss: 0.852153, acc.: 26.52%] [G loss: 0.761277]


/usr/local/lib/python3.5/dist-packages/keras/engine/training.py:490: UserWarning: Discrepancy between trainable weights and collected trainable weights, did you set `model.trainable` without calling `model.compile` after ?
  'Discrepancy between trainable weights and collected trainable'


1 [D loss: 0.425845, acc.: 75.00%] [G loss: 0.779853]
2 [D loss: 0.343837, acc.: 80.68%] [G loss: 0.887227]
3 [D loss: 0.299894, acc.: 88.64%] [G loss: 0.976111]
4 [D loss: 0.271564, acc.: 92.42%] [G loss: 1.080035]
5 [D loss: 0.243193, acc.: 96.21%] [G loss: 1.182428]
6 [D loss: 0.208229, acc.: 97.73%] [G loss: 1.292109]
7 [D loss: 0.200474, acc.: 98.48%] [G loss: 1.343504]
8 [D loss: 0.187413, acc.: 99.24%] [G loss: 1.419450]
9 [D loss: 0.171558, acc.: 99.62%] [G loss: 1.501104]
10 [D loss: 0.158099, acc.: 98.86%] [G loss: 1.640405]
11 [D loss: 0.134356, acc.: 100.00%] [G loss: 1.724208]
12 [D loss: 0.130538, acc.: 100.00%] [G loss: 1.790819]
13 [D loss: 0.120192, acc.: 100.00%] [G loss: 1.852412]
14 [D loss: 0.109628, acc.: 100.00%] [G loss: 1.985167]
15 [D loss: 0.089924, acc.: 100.00%] [G loss: 2.002176]
16 [D loss: 0.095063, acc.: 100.00%] [G loss: 2.052598]
17 [D loss: 0.086014, acc.: 100.00%] [G loss: 2.148647]
18 [D loss: 0.077523, acc.: 100.00%] [G loss: 2.218858]
19 [D loss:

...

63157 [D loss: 0.660268, acc.: 62.12%] [G loss: 0.987824]
63158 [D loss: 0.596280, acc.: 65.53%] [G loss: 1.063983]
63159 [D loss: 0.629443, acc.: 64.77%] [G loss: 1.102581]
63160 [D loss: 0.632974, acc.: 64.02%] [G loss: 1.083829]
63161 [D loss: 0.633150, acc.: 64.02%] [G loss: 1.012572]
63162 [D loss: 0.613224, acc.: 61.36%] [G loss: 1.012099]
63163 [D loss: 0.612516, acc.: 65.15%] [G loss: 1.074619]
63164 [D loss: 0.623327, acc.: 65.91%] [G loss: 1.010244]
63165 [D loss: 0.612985, acc.: 63.64%] [G loss: 0.971756]
63166 [D loss: 0.610382, acc.: 63.26%] [G loss: 1.011591]
63167 [D loss: 0.598937, acc.: 67.42%] [G loss: 1.027724]
63168 [D loss: 0.605438, acc.: 67.42%] [G loss: 1.071148]
63169 [D loss: 0.624320, acc.: 64.77%] [G loss: 1.064367]
63170 [D loss: 0.583866, acc.: 70.08%] [G loss: 1.059526]
63171 [D loss: 0.613175, acc.: 64.02%] [G loss: 0.991024]
63172 [D loss: 0.618029, acc.: 65.91%] [G loss: 1.085061]
63173 [D loss: 0.608968, acc.: 68.18%] [G loss: 1.057909]
63174 [D loss:

63301 [D loss: 0.599933, acc.: 69.32%] [G loss: 1.071213]
63302 [D loss: 0.630742, acc.: 64.39%] [G loss: 1.119082]
63303 [D loss: 0.656150, acc.: 57.20%] [G loss: 0.964321]
63304 [D loss: 0.591774, acc.: 65.53%] [G loss: 1.089187]
63305 [D loss: 0.608641, acc.: 66.67%] [G loss: 0.987634]
63306 [D loss: 0.570161, acc.: 71.97%] [G loss: 1.072435]
63307 [D loss: 0.618519, acc.: 65.15%] [G loss: 1.069012]
63308 [D loss: 0.619157, acc.: 66.29%] [G loss: 1.039392]
63309 [D loss: 0.620471, acc.: 64.39%] [G loss: 0.953325]
63310 [D loss: 0.632663, acc.: 62.50%] [G loss: 1.072978]
63311 [D loss: 0.629516, acc.: 63.64%] [G loss: 1.053700]
63312 [D loss: 0.593602, acc.: 67.05%] [G loss: 1.082730]
63313 [D loss: 0.582900, acc.: 72.73%] [G loss: 1.073334]
63314 [D loss: 0.616737, acc.: 64.77%] [G loss: 1.004222]
63315 [D loss: 0.605608, acc.: 67.05%] [G loss: 1.045670]
63316 [D loss: 0.586808, acc.: 68.56%] [G loss: 0.986814]
63317 [D loss: 0.598952, acc.: 64.02%] [G loss: 1.037906]
63318 [D loss:

63446 [D loss: 0.571691, acc.: 70.83%] [G loss: 0.993756]
63447 [D loss: 0.601764, acc.: 67.05%] [G loss: 1.005828]
63448 [D loss: 0.609000, acc.: 66.67%] [G loss: 0.969926]
63449 [D loss: 0.611531, acc.: 67.80%] [G loss: 0.968697]
63450 [D loss: 0.617112, acc.: 64.02%] [G loss: 1.015920]
63451 [D loss: 0.629366, acc.: 64.77%] [G loss: 1.029299]
63452 [D loss: 0.579702, acc.: 68.94%] [G loss: 1.024295]
63453 [D loss: 0.592905, acc.: 67.05%] [G loss: 1.098709]
63454 [D loss: 0.627679, acc.: 63.26%] [G loss: 1.046984]
63455 [D loss: 0.587835, acc.: 66.29%] [G loss: 1.025609]
63456 [D loss: 0.565033, acc.: 70.83%] [G loss: 1.033115]
63457 [D loss: 0.589319, acc.: 68.56%] [G loss: 1.038923]
63458 [D loss: 0.598289, acc.: 64.02%] [G loss: 0.988444]
63459 [D loss: 0.596668, acc.: 67.42%] [G loss: 0.985967]
63460 [D loss: 0.624614, acc.: 65.15%] [G loss: 1.029741]
63461 [D loss: 0.601911, acc.: 67.05%] [G loss: 0.978647]
63462 [D loss: 0.627813, acc.: 62.88%] [G loss: 1.067229]
63463 [D loss:

63588 [D loss: 0.592266, acc.: 70.45%] [G loss: 1.029032]
63589 [D loss: 0.597933, acc.: 68.18%] [G loss: 0.996716]
63590 [D loss: 0.595271, acc.: 64.77%] [G loss: 1.045655]
63591 [D loss: 0.657759, acc.: 57.58%] [G loss: 1.085870]
63592 [D loss: 0.606290, acc.: 68.56%] [G loss: 1.021178]
63593 [D loss: 0.577350, acc.: 69.32%] [G loss: 1.021105]
63594 [D loss: 0.614144, acc.: 65.53%] [G loss: 1.043333]
63595 [D loss: 0.634264, acc.: 63.26%] [G loss: 1.069094]
63596 [D loss: 0.628231, acc.: 65.91%] [G loss: 1.081419]
63597 [D loss: 0.604013, acc.: 64.39%] [G loss: 1.082809]
63598 [D loss: 0.641859, acc.: 59.47%] [G loss: 1.017812]
63599 [D loss: 0.608732, acc.: 68.94%] [G loss: 1.044369]
63600 [D loss: 0.598513, acc.: 67.42%] [G loss: 1.061725]
63601 [D loss: 0.591239, acc.: 68.18%] [G loss: 1.069991]
63602 [D loss: 0.609623, acc.: 65.15%] [G loss: 0.999211]
63603 [D loss: 0.618813, acc.: 68.18%] [G loss: 1.038031]
63604 [D loss: 0.633098, acc.: 62.50%] [G loss: 1.050991]
63605 [D loss:

63731 [D loss: 0.607468, acc.: 64.02%] [G loss: 1.061645]
63732 [D loss: 0.585013, acc.: 68.94%] [G loss: 1.016302]
63733 [D loss: 0.595388, acc.: 65.53%] [G loss: 1.026175]
63734 [D loss: 0.599774, acc.: 65.91%] [G loss: 1.074683]
63735 [D loss: 0.635051, acc.: 62.50%] [G loss: 0.977990]
